# Семинар 7. 
## Нестандартные ситуации

In [1]:
# импорт необходимых библиотек
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from tqdm import tqdm

import scipy.stats as st
from statsmodels.stats.power import tt_ind_solve_power
from statsmodels.stats.power import zt_ind_solve_power
from statsmodels.stats.proportion import proportion_effectsize
from statsmodels.stats import proportion
from statsmodels.stats.meta_analysis import effectsize_smd

### Задание 1
Мы провели А/А тест, в котором сравнивали одну и ту же версию сайта. Полученные результаты выглядят следующим образом. Можем ли мы на основе проведенного А/А теста запустить А/В-тестирование? Используйте уровень доверия 95%.

|                | **Версия А1** | **Версия А2** |
|:--------------:|:------------:|:------------:|
|   **Выборка**  |     1731     |     1702     |
| **Транзакция** |      152     |      189     |

In [2]:
# Задаем начальные параметры
alpha = .05
prob_1, prob_2 = 152 / 1731, 189 / 1702
sample_1_size, sample_2_size = 1731, 1702
# Генерируем распределение
a = st.bernoulli.rvs(p=prob_1, size=sample_1_size, random_state=12)
b = st.bernoulli.rvs(p=prob_2, size=sample_2_size, random_state=25)

In [13]:
st.bernoulli.rvs(p=prob_2, size=sample_2_size).sum()

175

In [12]:
# Сравнение хи2 и z
chi_value, p_value_chi2, table = proportion.proportions_chisquare([a.sum(), b.sum()], [a.size, b.size])
z_value, p_value_z = proportion.proportions_ztest([a.sum(), b.sum()], [a.size, b.size])
print(p_value_chi2, p_value_z)

0.02286339922157709 0.02286339922157713


In [4]:
# Считаем статистику по выборкам
chi_value, p_value, table = proportion.proportions_chisquare([a.sum(), b.sum()], [a.size, b.size])

se = np.sqrt((prob_1 * (1 - prob_1) / a.size) + (prob_2 * (1 - prob_2) / b.size))
md = a.mean() - b.mean()
left = md - 1.96 * se
right = md + 1.96 * se

print(f"Mean difference: {np.round(md, 5)}, p-value: {p_value} and confidence interval is: [{np.round(left, 5)}, {np.round(right, 5)}]")

if p_value < alpha and not min(left, right) < 0 < max(left, right):
    print(f"Sample # {1 if md > 0 else 2} mean is greater")
else:
    print("No significant difference")

Mean difference: -0.02324, p-value: 0.02286339922157709 and confidence interval is: [-0.04325, -0.00322]
Sample # 2 mean is greater


In [14]:
# Альтернативный способ через бутсрап
booted_diff = []   # массив для разницы средних
booted_pvalue = [] # массив для p-value по средним
size = max(a.size, b.size)
for _ in tqdm(range(10_000)):
    a_s = st.bernoulli.rvs(p=prob_1, size=size)   # бутстрапируем первую выборку
    b_s = st.bernoulli.rvs(p=prob_2, size=size)   # бутстрапируем вторую выборку
    booted_diff.append(np.mean(a_s - b_s))        # считаепм между ними среднюю разницу и записываем в массив
    booted_pvalue.append(proportion.proportions_chisquare([a_s.sum(), b_s.sum()], [a_s.size, b_s.size])[1])  # на каждой интерации считаем значение p-value

md_ci, std_ci = np.mean(booted_diff), np.std(booted_diff, ddof=1)
left_ci, right_ci = np.percentile(booted_diff, [2.5, 97.5])
p_value_ci = 2 * (1 - st.norm.cdf(np.abs(md_ci / std_ci)))                          

100%|███████████████████████████████████████████████████████████████████████████| 10000/10000 [00:10<00:00, 975.64it/s]


In [15]:
# Доверительный интервал разниц между группами
print(f"Mean difference: {np.round(md_ci, 5)}, p-value: {p_value_ci} and confidence interval is: [{np.round(left_ci, 5)}, {np.round(right_ci, 5)}]")

if p_value_ci < alpha and not min(left_ci, right_ci) < 0 < max(left_ci, right_ci):
    print(f"Sample # {1 if md_ci > 0 else 2} mean is greater")
else:
    print("No significant difference")

Mean difference: -0.02309, p-value: 0.02365121532037584 and confidence interval is: [-0.04333, -0.00289]
Sample # 2 mean is greater


In [16]:
# Ошибка первого рода, которая говорит нам о том, что группы различаются между собой!
np.mean(np.array(booted_pvalue) < 0.05) # FPR

0.6194

In [17]:
fig = make_subplots(rows=2, cols=1)

fig.add_trace(
    go.Histogram(x=booted_pvalue, name='booted_pvalue',),
    row=1, col=1
)

fig.add_trace(
    go.Histogram(x=booted_diff, name='booted_diff',),
    row=2, col=1
)

fig.update_layout(height=800, width=1000, title_text="After bootstrap")
fig.show()

### Задание 2
Мы провели А/А тест, в котором сравнивали одну и ту же версию сайта. Полученные результаты выглядят следующим образом. Можем ли мы на основе проведенного А/А теста запустить А/В-тестирование? Используйте уровень доверия 95%.  

|                             | **Версия А1** | **Версия А2** |
|:---------------------------:|:-------------:|:-------------:|
|         **Среднее**         |     38.175    |     33.710    |
| **Стандартное  отклонение** |       28      |       11      |
|         **Выборка**         |      108      |      105      |

In [18]:
# Вводим исходные данные по выборкам
alpha = .05
sample_1_mean, sample_2_mean = 38.175, 38.710 
sample_1_se, sample_2_se = 28, 11
sample_1_size, sample_2_size = 1080, 1050
# Генерируем нормальное распределение на основе введенных данных
norm_1 = st.norm(loc=sample_1_mean, scale=sample_1_se).rvs(size=sample_1_size, random_state=42)
norm_2 = st.norm(loc=sample_2_mean, scale=sample_2_se).rvs(size=sample_2_size, random_state=42)

In [19]:
# Вводим исходные данные по выборкам
alpha = .05
sample_1_mean, sample_2_mean = 38.175, 38.710 
sample_1_se, sample_2_se = 28, 11
sample_1_size, sample_2_size = 1080, 1050
# Генерируем нормальное распределение на основе введенных данных
norm_1 = st.expon(loc=sample_1_mean, scale=sample_1_se).rvs(size=sample_1_size, random_state=42)
norm_2 = st.expon(loc=sample_2_mean, scale=sample_2_se).rvs(size=sample_2_size, random_state=42)

In [20]:
fig = go.Figure()
fig.add_trace(go.Histogram(x=norm_1, name='norm_1'))
fig.add_trace(go.Histogram(x=norm_2, name='norm_2'))

# Overlay both histograms
fig.update_layout(barmode='overlay')
# Reduce opacity to see both histograms
fig.update_traces(opacity=0.5)
fig.show()

In [21]:
# Считаем статистику по выборкам
tvalue, pvalue = st.ttest_ind(norm_1, norm_2, equal_var=False, alternative='two-sided')
md = sample_1_mean - sample_2_mean

left, right = st.norm.interval(.95, loc=md, scale=se)
print(f"Mean difference: {np.round(md, 5)}, p-value: {p_value} and confidence interval is: [{np.round(left, 5)}, {np.round(right, 5)}]")

if p_value < alpha and not min(left, right) < 0 < max(left, right):
    print(f"Sample # {1 if md > 0 else 2} mean is greater")
else:
    print("No significant difference")

Mean difference: -0.535, p-value: 0.02286339922157709 and confidence interval is: [-0.55501, -0.51499]
Sample # 2 mean is greater


In [22]:
# Альтернативный способ через бутсрап
booted_diff = []
booted_pvalue = []
size = max(norm_1.size, norm_2.size)
for _ in tqdm(range(10_000)):
    a_s = np.random.choice(norm_1, size=size, replace=True)
    b_s = np.random.choice(norm_2, size=size, replace=True)
    booted_diff.append(np.mean(a_s - b_s))
    booted_pvalue.append(st.ttest_ind(a_s, b_s, equal_var=False, alternative='two-sided')[1])

# Доверительный интервал разниц между группами
md_ci, std_ci = np.mean(booted_diff), np.std(booted_diff, ddof=1)
left_ci, right_ci = np.percentile(booted_diff, [2.5, 97.5])
p_value_ci = 2 * (1 - st.norm.cdf(np.abs(md_ci / std_ci)))

100%|██████████████████████████████████████████████████████████████████████████| 10000/10000 [00:08<00:00, 1166.70it/s]


In [23]:
print(f"Mean difference: {np.round(md_ci, 5)}, p-value: {p_value_ci} and confidence interval is: [{np.round(left_ci, 5)}, {np.round(right_ci, 5)}]")

if p_value_ci < alpha and not min(left_ci, right_ci) < 0 < max(left_ci, right_ci):
    print(f"Sample # {1 if md_ci > 0 else 2} mean is greater")
else:
    print("No significant difference")

Mean difference: 16.38634, p-value: 0.0 and confidence interval is: [14.61464, 18.16625]
Sample # 1 mean is greater


In [24]:
# Ошибка первого рода, которая говорит нам о том, что группы почти не различаются между собой!
np.mean(np.array(booted_pvalue) < 0.05) # FPR

1.0

In [25]:
fig = make_subplots(rows=2, cols=1)

fig.add_trace(
    go.Histogram(x=booted_pvalue, name='booted_pvalue',),
    row=1, col=1
)

fig.add_trace(
    go.Histogram(x=booted_diff, name='booted_diff',),
    row=2, col=1
)

fig.update_layout(height=800, width=1000, title_text="After bootstrap")
fig.show()

### Задание 3. 
Мы запустили A/B-тест. На его проведение мы собираемся потратить 1 неделю, на каждую выборку направить по 10000 юзеров. На третий день, продакт посмотрел на промежуточные результаты. На этот момент в каждой выборке было по 3000 юзеров, а результат в конверсиях был статистически значимым в пользу версии B.    
Можем ли мы на основе таких данных выпустить версию B на всех юзеров?

### Задание 4. 
Мы провели А/А тест, в котором сравнивали одну и ту же версию сайта. Полученные результаты выглядят следующим образом. Можем ли мы на основе проведенного А/А теста запустить А/В-тестирование? Используйте уровень доверия 95%.  

|                          | **Версия А1** | **Версия A2** |
|:------------------------:|:------------:|:------------:|
|       **Посещение**      |     6351     |     6442     |
| **Добавление в корзину** |     1754     |     1902     |
| **Подтверждение заказа** |     1025     |     1099     |
|      **Транзакция**      |      623     |      642     |

In [46]:
# Задаем начальные параметры для добавления в корзину
alpha = .05
sample_1_size, sample_2_size = 6351, 6442
prob_1, prob_2 = 1754 / sample_1_size, 1902 / sample_2_size
# Генерируем распределение
a = st.bernoulli.rvs(p=prob_1, size=sample_1_size, random_state=12)
b = st.bernoulli.rvs(p=prob_2, size=sample_2_size, random_state=25)

In [47]:
# Альтернативный способ через бутсрап
booted_diff = []   # массив для разницы средних
booted_pvalue = [] # массив для 
size = max(a.size, b.size)
for _ in tqdm(range(10_000)):
    a_s = st.bernoulli.rvs(p=prob_1, size=size)
    b_s = st.bernoulli.rvs(p=prob_2, size=size)
    booted_diff.append(np.mean(a_s - b_s))
    booted_pvalue.append(proportion.proportions_chisquare([a_s.sum(), b_s.sum()], [a_s.size, b_s.size])[1])

md_ci, std_ci = np.mean(booted_diff), np.std(booted_diff, ddof=1)
left_ci, right_ci = np.percentile(booted_diff, [2.5, 97.5])
p_value_ci = 2 * (1 - st.norm.cdf(np.abs(md_ci / std_ci))) 

100%|███████████████████████████████████████████████████████████████████████████| 10000/10000 [00:11<00:00, 867.84it/s]


In [48]:
# Доверительный интервал разниц между группами
print(f"Mean difference: {np.round(md_ci, 5)}, p-value: {p_value_ci} and confidence interval is: [{np.round(left_ci, 5)}, {np.round(right_ci, 5)}]")

if p_value_ci < alpha and not min(left_ci, right_ci) < 0 < max(left_ci, right_ci):
    print(f"Sample # {1 if md_ci > 0 else 2} mean is greater")
else:
    print("No significant difference")

Mean difference: -0.0191, p-value: 0.016696624566792995 and confidence interval is: [-0.03477, -0.00326]
Sample # 2 mean is greater


In [49]:
# Ошибка первого рода, которая говорит нам о том, что группы различаются между собой!
np.mean(np.array(booted_pvalue) < 0.05) # FPR

0.6721

In [30]:
fig = make_subplots(rows=2, cols=1)

fig.add_trace(
    go.Histogram(x=booted_pvalue, name='booted_pvalue',),
    row=1, col=1
)

fig.add_trace(
    go.Histogram(x=booted_diff, name='booted_diff',),
    row=2, col=1
)

fig.update_layout(height=800, width=1000, title_text="After bootstrap")
fig.show()

In [31]:
# Задаем начальные параметры для подтверждения заказа
alpha = .05
sample_1_size, sample_2_size = 6351, 6442
prob_1, prob_2 = 1025 / sample_1_size, 1099 / sample_2_size
# Генерируем распределение
a = st.bernoulli.rvs(p=prob_1, size=sample_1_size, random_state=12)
b = st.bernoulli.rvs(p=prob_2, size=sample_2_size, random_state=25)

In [32]:
# Альтернативный способ через бутсрап
booted_diff = []   # массив для разницы средних
booted_pvalue = [] # массив для 
size = max(a.size, b.size)
for _ in tqdm(range(10_000)):
    a_s = st.bernoulli.rvs(p=prob_1, size=size)
    b_s = st.bernoulli.rvs(p=prob_2, size=size)
    booted_diff.append(np.mean(a_s - b_s))
    booted_pvalue.append(proportion.proportions_chisquare([a_s.sum(), b_s.sum()], [a_s.size, b_s.size])[1])

md_ci, std_ci = np.mean(booted_diff), np.std(booted_diff, ddof=1)
left_ci, right_ci = np.percentile(booted_diff, [2.5, 97.5])
p_value_ci = 2 * (1 - st.norm.cdf(np.abs(md_ci / std_ci))) 

100%|███████████████████████████████████████████████████████████████████████████| 10000/10000 [00:15<00:00, 634.13it/s]


In [33]:
# Доверительный интервал разниц между группами
print(f"Mean difference: {np.round(md_ci, 5)}, p-value: {p_value_ci} and confidence interval is: [{np.round(left_ci, 5)}, {np.round(right_ci, 5)}]")

if p_value_ci < alpha and not min(left_ci, right_ci) < 0 < max(left_ci, right_ci):
    print(f"Sample # {1 if md_ci > 0 else 2} mean is greater")
else:
    print("No significant difference")

Mean difference: -0.00916, p-value: 0.16359652252611534 and confidence interval is: [-0.02204, 0.00373]
No significant difference


In [34]:
# Ошибка первого рода, которая говорит нам о том, что группы различаются между собой!
np.mean(np.array(booted_pvalue) < 0.05) # FPR

0.2853

In [35]:
fig = make_subplots(rows=2, cols=1)

fig.add_trace(
    go.Histogram(x=booted_pvalue, name='booted_pvalue',),
    row=1, col=1
)

fig.add_trace(
    go.Histogram(x=booted_diff, name='booted_diff',),
    row=2, col=1
)

fig.update_layout(height=800, width=1000, title_text="After bootstrap")
fig.show()

In [36]:
# Задаем начальные параметры для транзакций
alpha = .05
sample_1_size, sample_2_size = 6351, 6442
prob_1, prob_2 = 623 / sample_1_size, 642 / sample_2_size
# Генерируем распределение
a = st.bernoulli.rvs(p=prob_1, size=sample_1_size, random_state=12)
b = st.bernoulli.rvs(p=prob_2, size=sample_2_size, random_state=25)

In [37]:
# Альтернативный способ через бутсрап
booted_diff = []   # массив для разницы средних
booted_pvalue = [] # массив для 
size = max(a.size, b.size)
for _ in tqdm(range(10_000)):
    a_s = st.bernoulli.rvs(p=prob_1, size=size)
    b_s = st.bernoulli.rvs(p=prob_2, size=size)
    booted_diff.append(np.mean(a_s - b_s))
    booted_pvalue.append(proportion.proportions_chisquare([a_s.sum(), b_s.sum()], [a_s.size, b_s.size])[1])

md_ci, std_ci = np.mean(booted_diff), np.std(booted_diff, ddof=1)
left_ci, right_ci = np.percentile(booted_diff, [2.5, 97.5])
p_value_ci = 2 * (1 - st.norm.cdf(np.abs(md_ci / std_ci))) 

100%|███████████████████████████████████████████████████████████████████████████| 10000/10000 [00:15<00:00, 650.97it/s]


In [38]:
# Доверительный интервал разниц между группами
print(f"Mean difference: {np.round(md_ci, 5)}, p-value: {p_value_ci} and confidence interval is: [{np.round(left_ci, 5)}, {np.round(right_ci, 5)}]")

if p_value_ci < alpha and not min(left_ci, right_ci) < 0 < max(left_ci, right_ci):
    print(f"Sample # {1 if md_ci > 0 else 2} mean is greater")
else:
    print("No significant difference")

Mean difference: -0.00155, p-value: 0.7674385110482225 and confidence interval is: [-0.01195, 0.00869]
No significant difference


In [39]:
# Ошибка первого рода, которая говорит нам о том, что группы различаются между собой!
np.mean(np.array(booted_pvalue) < 0.05) # FPR

0.0584

In [40]:
fig = make_subplots(rows=2, cols=1)

fig.add_trace(
    go.Histogram(x=booted_pvalue, name='booted_pvalue',),
    row=1, col=1
)

fig.add_trace(
    go.Histogram(x=booted_diff, name='booted_diff',),
    row=2, col=1
)

fig.update_layout(height=800, width=1000, title_text="After bootstrap")
fig.show()